In [5]:
!pip install plotly

  Using cached plotly-5.14.1-py2.py3-none-any.whl (15.3 MB)
  Using cached tenacity-8.2.2-py3-none-any.whl (24 kB)


You should consider upgrading via the 'E:\Code\Projects\TimbreTransfer\midi-ddsp-main\venv\Scripts\python.exe -m pip install --upgrade pip' command.


In [1]:
import os
import platform
import sys

if platform.system() == 'Windows':
    midi_ddsp_module_path = os.path.abspath(os.path.join('../../'))
    ddsp_module_path = os.path.abspath(os.path.join('../../../ddsp-playground-2/'))
else:
    midi_ddsp_module_path = os.path.abspath(os.path.join('../../'))
    ddsp_module_path = os.path.abspath(os.path.join('../../../ddsp/ddsp-playground-2/'))

def apply_module_path(module_path):
    print(f"module_path={module_path}")
    if module_path not in sys.path:
      sys.path.append(module_path)
      print(f"appending {module_path} to sys.path")
    else:
      print(f"do not appending {module_path} to sys.path")

apply_module_path(midi_ddsp_module_path)
apply_module_path(ddsp_module_path)

import sys
if platform.system() != 'Windows':
    sparsenet_module_path_abs = '/ssd003/home/burakovr/projects/vova/envs/main/lib/python3.8/site-packages/'
    apply_module_path(sparsenet_module_path_abs)

import midi_ddsp

module_path=E:\Code\Projects\TimbreTransfer\midi-ddsp-main
do not appending E:\Code\Projects\TimbreTransfer\midi-ddsp-main to sys.path
module_path=E:\Code\Projects\TimbreTransfer\ddsp-playground-2
appending E:\Code\Projects\TimbreTransfer\ddsp-playground-2 to sys.path


E:\Code\Projects\TimbreTransfer\midi-ddsp-main\midi_ddsp\midi_ddsp_synthesize.py:27: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm
e:\code\projects\timbretransfer\midi-ddsp-main\venv\lib\site-packages\tensorflow_addons\utils\ensure_tf_install.py:53: UserWarning: Tensorflow Addons supports using Python ops for all Tensorflow versions above or equal to 2.6.0 and strictly below 2.9.0 (nightly versions are not supported). 
 The versions of TensorFlow you are currently using is 2.9.0 and is not supported. 
Some things might work, some things might not.
If you were to encounter a bug, do not file an issue.
If you want to make sure you're using a tested and supported configuration, either change the TensorFlow version or the TensorFlow Addons's version. 
You can find the compatibility matrix in TensorFlow Addon's readme:
https://github.com/tensorflow/addons


nn.py sys.path=['E:\\Code\\Projects\\TimbreTransfer\\midi-ddsp-main\\midi_ddsp\\colab', 'E:\\Code\\Projects\\TimbreTransfer\\midi-ddsp-main', 'E:\\Code\\Software\\Python38\\python38.zip', 'E:\\Code\\Software\\Python38\\DLLs', 'E:\\Code\\Software\\Python38\\lib', 'E:\\Code\\Software\\Python38', 'e:\\code\\projects\\timbretransfer\\midi-ddsp-main\\venv', '', 'e:\\code\\projects\\timbretransfer\\midi-ddsp-main\\venv\\lib\\site-packages', 'e:\\code\\projects\\timbretransfer\\midi-ddsp-main\\venv\\lib\\site-packages\\win32', 'e:\\code\\projects\\timbretransfer\\midi-ddsp-main\\venv\\lib\\site-packages\\win32\\lib', 'e:\\code\\projects\\timbretransfer\\midi-ddsp-main\\venv\\lib\\site-packages\\Pythonwin', 'E:\\Code\\Projects\\TimbreTransfer\\ddsp-playground-2', 'E:/Code/Projects/Coursework/ddsp-playground/ddsp-playground-2/Lib/site-packages']
0


In [2]:
#  Copyright 2022 The MIDI-DDSP Authors.
#  #
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#  #
#      http://www.apache.org/licenses/LICENSE-2.0
#  #
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.

"""Training code for Synthesis Generator."""

import tensorflow as tf
import time
import os
import sys
import logging
import argparse
import IPython

from keras.utils.layer_utils import print_summary
from livelossplot import PlotLosses

from midi_ddsp.data_handling.get_dataset import get_dataset
from midi_ddsp.utils.training_utils import print_hparams, set_seed, \
    save_results, str2bool
from midi_ddsp.utils.summary_utils import write_tensorboard_audio
#                          from midi_ddsp.hparams_synthesis_generator import hparams as hp
from midi_ddsp.hparams_synthesis_generator import hparams_debug as hp
from midi_ddsp.modules.recon_loss import ReconLossHelper
from midi_ddsp.modules.gan_loss import GANLossHelper
from midi_ddsp.modules.get_synthesis_generator import get_synthesis_generator, \
    get_fake_data_synthesis_generator
from midi_ddsp.modules.discriminator import Discriminator

from ddsp.colab.notebook_utils import play, specplot

In [3]:
hp.data_dir = '../../data/'
hp.batch_size = 1 # for saving to TFRecord purposes

In [4]:
# Load vn dataset.
training_data, length_training_data, evaluation_data, length_evaluation_data = get_dataset(hp, training_data_repeats=1)

In [5]:
eval_sample_batch = next(iter(evaluation_data))
train_sample_batch = next(iter(training_data))
logging.info('Data loaded! Data size: %s', str(length_training_data))

In [6]:
training_example = next(iter(training_data))
play(training_example['audio'])

In [7]:
hp.data_dir = '../../data_cl/'
hp.instrument = 'cl'

In [8]:
# Load vn dataset.
cl_training_data, cl_length_training_data, cl_evaluation_data, cl_length_evaluation_data = get_dataset(hp, training_data_repeats=1)

In [9]:
cl_eval_sample_batch = next(iter(cl_evaluation_data))
cl_train_sample_batch = next(iter(cl_training_data))
logging.info('Clarinet data loaded! Data size: %s', str(cl_length_training_data))

In [10]:
cl_training_example = next(iter(cl_training_data))
play(cl_training_example['audio'])

In [11]:
hp.reverb_length = 16000

In [12]:
midi_ddsp_model = get_synthesis_generator(hp)
midi_ddsp_model(eval_sample_batch)
midi_ddsp_model.summary()

MIDIExpressionAE.__call__()
SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()
debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(3, 1000, 1), dtype=float32, numpy=
array([[[316.42538],
        [316.4605 ],
        [316.4141 ],
        ...,
        [373.20862],
        [373.60303],
        [373.6359 ]],

       [[367.1112 ],
        [367.04114],
        [366.97314],
        ...,
        [589.61584],
        [588.9996 ],
        [588.36633]],

       [[293.9236 ],
        [293.9281 ],
        [293.85327],
        ...,
        [370.82068],
        [370.9535 ],
        [370.99457]]], dtype=float32)>, 'amplitudes': <tf.Tensor: shape=(3, 1000, 1), dtype=float32, numpy=
array([[[1.02393   ],
        [1.0065366 ],
        [0.9924545 ],
        ...,
        [0.91414106],
        [0.9056382 ],
        [0.89671147]],

       [[1.0259533 ],
        [1.0088432 ],
        [0.9943401 ],
        ...,
        [0.91659516],
  

In [13]:
midi_ddsp_model.load_weights('logs/logs_synthesis_generator/experiment_5/e24_s4655')

In [98]:
tf.keras.Model.summary(midi_ddsp_model, expand_nested=False)

Model: "midi_expression_ae"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 synth_coder (SynthCoder)    multiple                  7119550   
                                                                 
 expression_midi_decoder_1 (  multiple                 4305223   
 ExpressionMidiDecoder)                                          
                                                                 
 reverb_modules (ReverbModul  multiple                 16000     
 es)                                                             
                                                                 
 processor_group (ProcessorG  multiple                 0         
 roup)                                                           
                                                                 
Total params: 11,440,773
Trainable params: 11,436,933
Non-trainable params: 3,840
________________________________

In [14]:
synthcoder = midi_ddsp_model.synth_coder
tf.keras.Model.summary(synthcoder, expand_nested=True)

Model: "synth_coder"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 mel_f0ld_encoder (MelF0LDEn  multiple                 7054912   
 coder)                                                          
|¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯|
| cnn8 (Cnn8)               multiple                  4689984   |
||¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯||
|| conv_block (ConvBlock)  multiple                  37952     ||
|||¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯¯|||
||| conv2d (Conv2D)       multiple                  576       |||
|||                                                           |||
||| conv2d_1 (Conv2D)     multiple                  36864     |||
|||                                                           |||
||| batch_normalization (BatchN  multiple           256       |||
||| ormalization)                                      

In [15]:
play(midi_ddsp_model(training_example)['synth_audio'])

MIDIExpressionAE.__call__()
SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()
debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 1000, 1), dtype=float32, numpy=
array([[[399.05878],
        [399.35928],
        [399.66122],
        [399.95224],
        [400.2298 ],
        [400.50735],
        [400.5163 ],
        [400.5103 ],
        [400.54736],
        [400.63736],
        [400.72733],
        [400.57047],
        [400.4001 ],
        [400.18405],
        [399.9117 ],
        [399.63937],
        [399.53665],
        [399.44342],
        [399.10953],
        [398.48004],
        [397.85056],
        [397.10278],
        [396.3485 ],
        [395.71964],
        [395.24536],
        [394.7711 ],
        [394.70523],
        [394.66125],
        [394.67056],
        [394.74536],
        [394.82013],
        [394.99655],
        [395.17853],
        [395.3756 ],
        [395.59134],
        [395.80707],
  

In [16]:
play(midi_ddsp_model(training_example)['midi_audio']) # it is bugged in this checkpoint of the model (probably because the architecture has changed and weights are little bit off, or they're untrained, idk)

MIDIExpressionAE.__call__()
SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()
debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 1000, 1), dtype=float32, numpy=
array([[[399.05878],
        [399.35928],
        [399.66122],
        [399.95224],
        [400.2298 ],
        [400.50735],
        [400.5163 ],
        [400.5103 ],
        [400.54736],
        [400.63736],
        [400.72733],
        [400.57047],
        [400.4001 ],
        [400.18405],
        [399.9117 ],
        [399.63937],
        [399.53665],
        [399.44342],
        [399.10953],
        [398.48004],
        [397.85056],
        [397.10278],
        [396.3485 ],
        [395.71964],
        [395.24536],
        [394.7711 ],
        [394.70523],
        [394.66125],
        [394.67056],
        [394.74536],
        [394.82013],
        [394.99655],
        [395.17853],
        [395.3756 ],
        [395.59134],
        [395.80707],
  

In [17]:
print(synthcoder(cl_training_example).keys())

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()
dict_keys(['f0_hz', 'amplitudes', 'harmonic_distribution', 'noise_magnitudes'])


In [18]:
from midi_ddsp.utils.inference_utils import get_process_group

# processor groups with various frame sizes
processor_group_64      = get_process_group(n_frames=1000, frame_size=64, sample_rate=16000, use_angular_cumsum=False)
processor_group_128     = get_process_group(n_frames=500, frame_size=128, sample_rate=16000, use_angular_cumsum=False)
processor_group_256     = get_process_group(n_frames=250, frame_size=256, sample_rate=16000, use_angular_cumsum=False)
processor_group_512     = get_process_group(n_frames=125, frame_size=512, sample_rate=16000, use_angular_cumsum=False)
processor_group_1024    = get_process_group(n_frames=62, frame_size=1024, sample_rate=16000, use_angular_cumsum=False)

In [19]:
def get_audio(synthcoder_output, processor_group):
    my_control_params = processor_group.get_controls(synthcoder_output, verbose=False)
    my_synth_audio = processor_group.get_signal(my_control_params)
    return my_synth_audio

def downsample_tensor(tensor, factor):
    batch_size, time_length, n = tensor.shape
    assert time_length % factor == 0, "Time axis length must be divisible by the downsample factor."

    # Reshape the tensor to prepare for downsampling
    tensor_reshaped = tf.reshape(tensor, [batch_size, time_length // factor, factor, n])

    # Take the mean along the new axis, which was originally the time axis
    downsampled_tensor = tf.reduce_mean(tensor_reshaped, axis=2)

    return downsampled_tensor

def downsample_synth_params(synth_params: dict, factor):
    if factor > 1:
        return {k: downsample_tensor(v, factor) for k, v in synth_params.items()}
    else:
        return synth_params

In [20]:
input_tensor = cl_training_example['f0_hz']  # 10: batch_size, 1000: time_length, 5: n
downsampled_tensor = downsample_tensor(input_tensor, factor=2)
print("Original tensor shape:", input_tensor.shape)
print("Downsampled tensor shape:", downsampled_tensor.shape)



Original tensor shape: (1, 1000, 1)
Downsampled tensor shape: (1, 500, 1)


In [33]:
import numpy as np
import plotly.graph_objects as go

def plot_tensor_as_image(tensor):
    # Ensure the tensor is a NumPy array
    tensor_np = tensor.numpy()

    # Combine the batch_size and n dimensions into a single dimension
    combined_shape = (tensor_np.shape[0] * tensor_np.shape[2], tensor_np.shape[1])
    tensor_2d = tensor_np.reshape(combined_shape)

    # Create a heatmap using Plotly
    fig = go.Figure(go.Heatmap(z=tensor_2d, colorscale='Viridis'))

    # Customize the axis labels and title
    fig.update_layout(
        xaxis_title="Time",
        yaxis_title="Channels",
        title="Tensor Visualization",
        width=32*37,  # Width in pixels (32 inches * 37 pixels per inch)
        height=10*37,  # Height in pixels (10 inches * 37 pixels per inch)
        autosize=False
    )

    # Display the visualization
    fig.show()

def line_plot_tensor_2d(tensor, title=""):
    # Convert the tensor to a 1D array
    fundamental_frequencies = tf.squeeze(tensor)

    # Create the time axis
    time_axis = np.arange(0, len(fundamental_frequencies))

    # Create a line plot using Plotly
    fig = go.Figure(go.Scatter(x=time_axis, y=fundamental_frequencies, mode='lines'))

    # Customize the axis labels and title
    fig.update_layout(
        xaxis_title="Frames",
        yaxis_title="Fundamental Frequency (f0_hz)",
        title=title,
        width=32*37,  # Width in pixels (32 inches * 37 pixels per inch)
        height=10*37,  # Height in pixels (10 inches * 37 pixels per inch)
        autosize=False
    )

    # Display the visualization
    fig.show()

In [34]:
plot_tensor_as_image(input_tensor)
line_plot_tensor_2d(input_tensor, title="Original tensor")

In [36]:
plot_tensor_as_image(downsampled_tensor)
line_plot_tensor_2d(downsampled_tensor, title="Downsampled tensor")

In [88]:
def test_synthcoder_resolution(synthcoder_model, input_dict, downsample_factor, title):
    output = downsample_synth_params(synthcoder_model(input_dict), factor=downsample_factor)

    line_plot_tensor_2d(output['f0_hz'], title=title)

    processor_group = get_process_group(n_frames=1000//downsample_factor,
                                        frame_size=64*downsample_factor,
                                        sample_rate=16000,
                                        use_angular_cumsum=False)

    audio = get_audio(synthcoder_output=output,
                      processor_group=processor_group)

    play(audio)
    return audio

In [89]:
import librosa
from copy import deepcopy

def read_wav(filename, dir='../../data_synths', target_sample_rate = 16000):
    audio_file = os.path.join(dir, filename)
    audio_data, original_sample_rate = librosa.load(audio_file, sr=None)

    resampled_audio_data = librosa.resample(audio_data, original_sample_rate, target_sample_rate)
    #resampled_audio_data = audio_data

    # Convert the resampled audio data to a TensorFlow tensor
    resampled_audio_tensor = tf.convert_to_tensor(resampled_audio_data, dtype=tf.float32)

    return resampled_audio_tensor


In [94]:

cl_training_example_oct_up = deepcopy(cl_training_example)
cl_training_example_oct_up['f0_hz'] = 2 * cl_training_example_oct_up['f0_hz']

cl_training_example_oct_up_pw2 = deepcopy(cl_training_example_oct_up)
cl_training_example_oct_up_pw2['audio'] = tf.random.uniform(tf.shape(cl_training_example_oct_up_pw2['audio']))

cl_training_example_replaced_urmp_violin = deepcopy(cl_training_example)
cl_training_example_replaced_urmp_violin['audio'] = training_example['audio']

cl_training_example_oct_up_replaced_urmp_violin = deepcopy(cl_training_example_oct_up)
cl_training_example_oct_up_replaced_urmp_violin['audio'] = training_example['audio']

pluck_arpeggio = read_wav('pluck_arpeggio.wav')
cl_training_example_oct_up_replaced_audio_pluck_arpeggio = deepcopy(cl_training_example_oct_up)
cl_training_example_oct_up_replaced_audio_pluck_arpeggio['audio'] = tf.reshape(pluck_arpeggio, [1, 64000])

pluck_arpeggio_bass = read_wav('pluck_arpeggio_bass.wav')
cl_training_example_oct_up_replaced_audio_pluck_arpeggio_bass = deepcopy(cl_training_example_oct_up)
cl_training_example_oct_up_replaced_audio_pluck_arpeggio_bass['audio'] = tf.reshape(pluck_arpeggio_bass, [1, 64000])

vn_orchestra_downward = read_wav('vn_orchestra_downward.wav')
cl_training_example_oct_up_replaced_audio_vn_orchestra_downward = deepcopy(cl_training_example_oct_up)
cl_training_example_oct_up_replaced_audio_vn_orchestra_downward['audio'] = tf.reshape(vn_orchestra_downward, [1, 64000])

samples_to_run = {
    'urmp clarinet': cl_training_example,
    'urmp clarinet octave up': cl_training_example_oct_up,
    'urmp clarinet octave up very loud': cl_training_example_oct_up_pw2,
    'urmp clarinet with audio of urmp violin': cl_training_example_replaced_urmp_violin,
    'urmp clarinet octave up with audio of urmp violin': cl_training_example_oct_up_replaced_urmp_violin,
    'urmp clarinet octave up with audio of pluck arp synth': cl_training_example_oct_up_replaced_audio_pluck_arpeggio,
    'urmp clarinet octave up with audio of bass pluck arp synth': cl_training_example_oct_up_replaced_audio_pluck_arpeggio_bass,
    'urmp clarinet octave up with audio of kontakt vn orchestra': cl_training_example_oct_up_replaced_audio_vn_orchestra_downward
}

C:\Users\vovab\AppData\Local\Temp\ipykernel_59328\1395512016.py:8: FutureWarning:

Pass orig_sr=48000, target_sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error



In [96]:
for k, test_sample in samples_to_run.items():

    test_synthcoder_resolution(synthcoder_model=synthcoder,
                               input_dict=test_sample,
                               downsample_factor=8,
                               title=k)

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 125, 1), dtype=float32, numpy=
array([[[350.94446],
        [351.03262],
        [350.61475],
        [350.57806],
        [350.73468],
        [350.7289 ],
        [350.70203],
        [350.6708 ],
        [350.61624],
        [350.70032],
        [350.62878],
        [350.8246 ],
        [350.94287],
        [351.1054 ],
        [351.1305 ],
        [351.34   ],
        [351.55188],
        [351.57355],
        [351.56216],
        [351.57806],
        [351.61917],
        [351.74274],
        [351.66953],
        [351.62146],
        [351.43228],
        [354.50787],
        [329.71124],
        [298.86542],
        [296.22934],
        [295.15353],
        [294.6712 ],
        [294.52347],
        [294.63528],
        [294.631  ],
        [294.58044],
        [294.56622],
        [294.53836],
        [294.50104],
        [294.38885],
        [294.31293],
        [294.24066],
   

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 125, 1), dtype=float32, numpy=
array([[[701.8889 ],
        [702.06525],
        [701.2295 ],
        [701.1561 ],
        [701.46936],
        [701.4578 ],
        [701.40405],
        [701.3416 ],
        [701.2325 ],
        [701.40063],
        [701.25757],
        [701.6492 ],
        [701.88574],
        [702.2108 ],
        [702.261  ],
        [702.68   ],
        [703.10376],
        [703.1471 ],
        [703.1243 ],
        [703.1561 ],
        [703.23834],
        [703.4855 ],
        [703.33905],
        [703.2429 ],
        [702.86456],
        [709.01575],
        [659.4225 ],
        [597.73083],
        [592.4587 ],
        [590.30707],
        [589.3424 ],
        [589.04694],
        [589.27057],
        [589.262  ],
        [589.1609 ],
        [589.13245],
        [589.0767 ],
        [589.0021 ],
        [588.7777 ],
        [588.62585],
        [588.4813 ],
   

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


...

debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 125, 1), dtype=float32, numpy=
array([[[701.8889 ],
        [702.06525],
        [701.2295 ],
        [701.1561 ],
        [701.46936],
        [701.4578 ],
        [701.40405],
        [701.3416 ],
        [701.2325 ],
        [701.40063],
        [701.25757],
        [701.6492 ],
        [701.88574],
        [702.2108 ],
        [702.261  ],
        [702.68   ],
        [703.10376],
        [703.1471 ],
        [703.1243 ],
        [703.1561 ],
        [703.23834],
        [703.4855 ],
        [703.33905],
        [703.2429 ],
        [702.86456],
        [709.01575],
        [659.4225 ],
        [597.73083],
        [592.4587 ],
        [590.30707],
        [589.3424 ],
        [589.04694],
        [589.27057],
        [589.262  ],
        [589.1609 ],
        [589.13245],
        [589.0767 ],
        [589.0021 ],
        [588.7777 ],
        [588.62585],
        [588.4813 ],
   

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 125, 1), dtype=float32, numpy=
array([[[701.8889 ],
        [702.06525],
        [701.2295 ],
        [701.1561 ],
        [701.46936],
        [701.4578 ],
        [701.40405],
        [701.3416 ],
        [701.2325 ],
        [701.40063],
        [701.25757],
        [701.6492 ],
        [701.88574],
        [702.2108 ],
        [702.261  ],
        [702.68   ],
        [703.10376],
        [703.1471 ],
        [703.1243 ],
        [703.1561 ],
        [703.23834],
        [703.4855 ],
        [703.33905],
        [703.2429 ],
        [702.86456],
        [709.01575],
        [659.4225 ],
        [597.73083],
        [592.4587 ],
        [590.30707],
        [589.3424 ],
        [589.04694],
        [589.27057],
        [589.262  ],
        [589.1609 ],
        [589.13245],
        [589.0767 ],
        [589.0021 ],
        [588.7777 ],
        [588.62585],
        [588.4813 ],
   

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 125, 1), dtype=float32, numpy=
array([[[701.8889 ],
        [702.06525],
        [701.2295 ],
        [701.1561 ],
        [701.46936],
        [701.4578 ],
        [701.40405],
        [701.3416 ],
        [701.2325 ],
        [701.40063],
        [701.25757],
        [701.6492 ],
        [701.88574],
        [702.2108 ],
        [702.261  ],
        [702.68   ],
        [703.10376],
        [703.1471 ],
        [703.1243 ],
        [703.1561 ],
        [703.23834],
        [703.4855 ],
        [703.33905],
        [703.2429 ],
        [702.86456],
        [709.01575],
        [659.4225 ],
        [597.73083],
        [592.4587 ],
        [590.30707],
        [589.3424 ],
        [589.04694],
        [589.27057],
        [589.262  ],
        [589.1609 ],
        [589.13245],
        [589.0767 ],
        [589.0021 ],
        [588.7777 ],
        [588.62585],
        [588.4813 ],
   

In [43]:
test_synthcoder_resolution(synthcoder_model=synthcoder,
                           input_dict=cl_training_example,
                           downsample_factor=2)

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 500, 1), dtype=float32, numpy=
array([[[350.85846],
        [350.9204 ],
        [350.9854 ],
        [351.0136 ],
        [351.02252],
        [351.08685],
        [351.16394],
        [350.85718],
        [350.61273],
        [350.59357],
        [350.64777],
        [350.60498],
        [350.5816 ],
        [350.5438 ],
        [350.5285 ],
        [350.65845],
        [350.76352],
        [350.7567 ],
        [350.7187 ],
        [350.69983],
        [350.72293],
        [350.74615],
        [350.73645],
        [350.71008],
        [350.6962 ],
        [350.73065],
        [350.72742],
        [350.65384],
        [350.6231 ],
        [350.66962],
        [350.7309 ],
        [350.6596 ],
        [350.61145],
        [350.5982 ],
        [350.6092 ],
        [350.64612],
        [350.7569 ],
        [350.77545],
        [350.69174],
        [350.57718],
        [350.5747 ],
   

<tf.Tensor: shape=(1, 64000), dtype=float32, numpy=
array([[ 0.00017274,  0.00028217,  0.00033901, ..., -0.00532449,
        -0.00685474, -0.00792648]], dtype=float32)>

In [44]:
test_synthcoder_resolution(synthcoder_model=synthcoder,
                           input_dict=cl_training_example,
                           downsample_factor=4)

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 250, 1), dtype=float32, numpy=
array([[[350.88943],
        [350.9995 ],
        [351.0547 ],
        [351.01056],
        [350.60315],
        [350.62637],
        [350.56268],
        [350.59348],
        [350.76013],
        [350.70926],
        [350.73456],
        [350.72327],
        [350.71344],
        [350.6906 ],
        [350.64636],
        [350.69525],
        [350.60483],
        [350.62766],
        [350.76617],
        [350.63446],
        [350.57864],
        [350.6789 ],
        [350.7946 ],
        [350.85455],
        [350.95392],
        [350.93182],
        [351.0993 ],
        [351.1115 ],
        [351.14615],
        [351.11484],
        [351.31384],
        [351.36615],
        [351.50937],
        [351.59442],
        [351.58224],
        [351.56488],
        [351.56976],
        [351.55457],
        [351.56363],
        [351.5925 ],
        [351.63293],
   

<tf.Tensor: shape=(1, 64000), dtype=float32, numpy=
array([[ 0.00062427,  0.00104884,  0.00129516, ..., -0.00204768,
        -0.00210796, -0.00286011]], dtype=float32)>

In [45]:
test_synthcoder_resolution(synthcoder_model=synthcoder,
                           input_dict=cl_training_example,
                           downsample_factor=8)

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 125, 1), dtype=float32, numpy=
array([[[350.94446],
        [351.03262],
        [350.61475],
        [350.57806],
        [350.73468],
        [350.7289 ],
        [350.70203],
        [350.6708 ],
        [350.61624],
        [350.70032],
        [350.62878],
        [350.8246 ],
        [350.94287],
        [351.1054 ],
        [351.1305 ],
        [351.34   ],
        [351.55188],
        [351.57355],
        [351.56216],
        [351.57806],
        [351.61917],
        [351.74274],
        [351.66953],
        [351.62146],
        [351.43228],
        [354.50787],
        [329.71124],
        [298.86542],
        [296.22934],
        [295.15353],
        [294.6712 ],
        [294.52347],
        [294.63528],
        [294.631  ],
        [294.58044],
        [294.56622],
        [294.53836],
        [294.50104],
        [294.38885],
        [294.31293],
        [294.24066],
   

<tf.Tensor: shape=(1, 64000), dtype=float32, numpy=
array([[1.1970608e-03, 1.9659982e-03, 2.2828663e-03, ..., 1.0246504e-03,
        7.3523074e-04, 8.2336075e-05]], dtype=float32)>

In [48]:
test_synthcoder_resolution(synthcoder_model=synthcoder,
                           input_dict=cl_training_example,
                           downsample_factor=20)

SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()


debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 50, 1), dtype=float32, numpy=
array([[[350.91144],
        [350.6504 ],
        [350.70163],
        [350.66568],
        [350.77213],
        [351.08075],
        [351.4732 ],
        [351.56906],
        [351.68448],
        [351.54962],
        [333.79218],
        [295.99478],
        [294.608  ],
        [294.60858],
        [294.53912],
        [294.38385],
        [294.21298],
        [294.3258 ],
        [294.54803],
        [294.69742],
        [294.92715],
        [295.1324 ],
        [294.83383],
        [291.5134 ],
        [279.64618],
        [277.95053],
        [277.96313],
        [277.94305],
        [277.96738],
        [277.96332],
        [277.96802],
        [278.01062],
        [277.98712],
        [277.91995],
        [277.53677],
        [277.59033],
        [276.49384],
        [292.64618],
        [294.81342],
        [294.3519 ],
        [294.37457],
    

<tf.Tensor: shape=(1, 64000), dtype=float32, numpy=
array([[0.00245539, 0.00393247, 0.00448458, ..., 0.00188244, 0.00167609,
        0.00159267]], dtype=float32)>

In [43]:
from copy import deepcopy

cl_training_example_with_vn_instrument = deepcopy(cl_training_example)
cl_training_example_with_vn_instrument['instrument_id'] = tf.constant([20])

print(cl_training_example['instrument_id'])
print(cl_training_example['instrument_id'].shape)
print(cl_training_example_with_vn_instrument['instrument_id'])
print(cl_training_example_with_vn_instrument['instrument_id'].shape)

play(midi_ddsp_model(cl_training_example)['synth_audio'])

tf.Tensor([6], shape=(1,), dtype=int32)
(1,)
tf.Tensor([20], shape=(1,), dtype=int32)
(1,)
MIDIExpressionAE.__call__()
SynthCoder.__call__()
MelF0LDEncoder.__call__()
FCHarmonicDecoder.__call__()
debug: DAGLayer(<class 'ddsp.processors.ProcessorGroup'>) received input={'f0_hz': <tf.Tensor: shape=(1, 1000, 1), dtype=float32, numpy=
array([[[  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.     ],
        [  0.   

In [ ]:
cl_training_example['f0_hz']